In [ ]:
!pip install nengo-dl

In [2]:
%matplotlib inline
import numpy as np
import nengo
import tensorflow as tf
from sklearn.utils import shuffle
import matplotlib.pyplot as plt

In [3]:
(train_img, train_label), (
    test_img,
    test_label,
) = tf.keras.datasets.fashion_mnist.load_data()

# split the dataset of 0 and 1 digits
train_img_0 = train_img[np.where(train_label == 0)]
train_img_1 = train_img[np.where(train_label == 1)]

test_img_0 = test_img[np.where(test_label == 0)]
test_img_1 = test_img[np.where(test_label == 1)]

# concatenate images
train_imgs = np.concatenate((train_img_0, train_img_1),axis = 0)
train_labels = np.concatenate((train_label[np.where(train_label == 0)],train_label[np.where(train_label== 1)]),axis = 0)

test_imgs = np.concatenate((test_img_0,test_img_1),axis = 0)
test_labels = np.concatenate((test_label[np.where(test_label == 0)],test_label[np.where(test_label== 1)]),axis = 0)

print(train_imgs.shape,train_labels.shape,test_imgs.shape,test_labels.shape)

4431872/4422102 [==============================] - 0s 0us/step
(12000, 28, 28) (12000,) (2000, 28, 28) (2000,)


In [4]:
# reshape train, test dataset
train_imgs = train_imgs.reshape((train_imgs.shape[0],28,28,1))
test_imgs = test_imgs.reshape((test_imgs.shape[0],28,28,1))

# change labels to one hot 
train_labels = tf.keras.utils.to_categorical(train_labels)
test_labels = tf.keras.utils.to_categorical(test_labels)


In [5]:
inp=tf.keras.layers.Input(shape=(28,28,1))

conv0 = tf.keras.layers.Conv2D(filters=8,kernel_size=3,padding="same", activation=tf.nn.relu)(inp)
pool0 = tf.keras.layers.MaxPooling2D(pool_size=2,strides=2)(conv0)

conv1 = tf.keras.layers.Conv2D(filters=16,kernel_size=3,padding="same", activation=tf.nn.relu)(pool0)
pool1 = tf.keras.layers.MaxPooling2D(pool_size=2,strides=2)(conv1)   

conv2 = tf.keras.layers.Conv2D(filters=32,kernel_size=3,padding="same", activation=tf.nn.relu)(pool1)
conv3 = tf.keras.layers.Conv2D(filters=16,kernel_size=1,padding="same", activation=tf.nn.relu)(conv2)
conv4 = tf.keras.layers.Conv2D(filters=32,kernel_size=3,padding="same", activation=tf.nn.relu)(conv3)   
pool2 = tf.keras.layers.MaxPooling2D(pool_size=2,strides=2)(conv4)

conv5 = tf.keras.layers.Conv2D(filters=64,kernel_size=3,padding="same", activation=tf.nn.relu)(pool2)
conv6 = tf.keras.layers.Conv2D(filters=32,kernel_size=1,padding="same", activation=tf.nn.relu)(conv5)
conv7 = tf.keras.layers.Conv2D(filters=64,kernel_size=3,padding="same", activation=tf.nn.relu)(conv6)   
pool3 = tf.keras.layers.MaxPooling2D(pool_size=2,strides=2)(conv7)
flatten = tf.keras.layers.Flatten()(pool3)
dense = tf.keras.layers.Dense(2,activation = 'softmax')(flatten)
model = tf.keras.Model(inputs = inp, outputs = dense)
model.summary()

Model: "model"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         [(None, 28, 28, 1)]       0         
_________________________________________________________________
conv2d (Conv2D)              (None, 28, 28, 8)         80        
_________________________________________________________________
max_pooling2d (MaxPooling2D) (None, 14, 14, 8)         0         
_________________________________________________________________
conv2d_1 (Conv2D)            (None, 14, 14, 16)        1168      
_________________________________________________________________
max_pooling2d_1 (MaxPooling2 (None, 7, 7, 16)          0         
_________________________________________________________________
conv2d_2 (Conv2D)            (None, 7, 7, 32)          4640      
_________________________________________________________________
conv2d_3 (Conv2D)            (None, 7, 7, 16)          528   

In [6]:
train = False
# if train == True, model will be trained and vice versa
if train:
  model.compile(optimizer = tf.keras.optimizers.RMSprop(0.001),
                loss= tf.keras.losses.CategoricalCrossentropy(),
                metrics = ['accuracy']
                )
  model.fit(train_imgs,train_labels,validation_data=(test_imgs,test_labels),epochs=5)
  model.save('cnn_snn.h5')
else:
  model = tf.keras.models.load_model('/content/drive/MyDrive/cnn_snn.h5')

In [7]:
# CNN is used to extract the features of the input images
# I get the output of the last convolution layer
output = model.layers[-4].output
model1 = tf.keras.Model(inputs=model.inputs, outputs=[output])

In [11]:
# feature map after predict
train_predict = model1.predict(train_imgs,batch_size=1)
test_predict = model1.predict(test_imgs,batch_size =1)

In [23]:
# flatten images
train_predict_flatten = train_predict.reshape(train_predict.shape[0],-1)
test_predict_flatten = test_predict.reshape(test_predict.shape[0],-1)

print(train_predict_flatten.shape)

(12000, 576)


In [13]:
import nengo_dl

In [36]:
presentation_time = 0.1
with nengo.Network(seed=0) as net:
    # set some default parameters for the neurons that will make
    # the training progress more smoothly
    net.config[nengo.Ensemble].max_rates = nengo.dists.Choice([100])
    net.config[nengo.Ensemble].intercepts = nengo.dists.Choice([0])
    net.config[nengo.Connection].synapse = None
    net.config[nengo.Connection].transform = nengo_dl.dists.Glorot()
    neuron_type = nengo.LIF(amplitude=0.01)

    # this is an optimization to improve the training speed,
    # since we won't require stateful behaviour in this example
    nengo_dl.configure_settings(stateful=False)

    # the input node that will be used to feed in input images
    inp = nengo.Node(nengo.processes.PresentInput(train_predict_flatten,presentation_time))
    layer_1 = nengo.Ensemble(6,dimensions=1)
    conn1 = nengo.Connection(inp,layer_1.neurons)
  
    layer_2 = nengo.Ensemble(3,dimensions = 1)
    weight1 = np.random.randn(layer_2.n_neurons,layer_1.n_neurons)
    print(weight1)
    conn2 = nengo.Connection(layer_1.neurons,layer_2.neurons, transform=weight1,learning_rule_type=nengo.PES(0.001))

    # layer_3 = nengo.Ensemble(2,dimensions = 1)
    # conn3 = nengo.Connection(layer_2,layer_3)

    # out = nengo.Node(size_in=2)
    # nengo.Connection(layer_3, out)
    
    out_p = nengo.Probe(layer_2, label="out_p")
    


[[-0.43007686  1.08339036  0.31989423  0.3963555   0.31898693 -1.16103692]
 [-1.35442212  2.002509    1.23284284  0.63697957 -0.3022611  -0.67961268]
 [-1.00877889  1.53977345 -0.41800346  0.50668087 -0.31507021 -0.35388518]]


In [38]:
with nengo.Simulator(net) as sim:
  sim.run(5)
  w2 = sim.data[conn2].weights
  print(w2)

HtmlProgressBar cannot be displayed. Please use the TerminalProgressBar. It can be enabled with `nengo.rc['progress']['progress_bar'] = 'nengo.utils.progress.TerminalProgressBar'`.

HtmlProgressBar cannot be displayed. Please use the TerminalProgressBar. It can be enabled with `nengo.rc['progress']['progress_bar'] = 'nengo.utils.progress.TerminalProgressBar'`.

[[-0.43007686  1.08339036  0.31989423  0.3963555   0.31898693 -1.16103692]
 [-1.35442212  2.002509    1.23284284  0.63697957 -0.3022611  -0.67961268]
 [-1.00877889  1.53977345 -0.41800346  0.50668087 -0.31507021 -0.35388518]]
